# TOUR GUIDE 
**Main Features**
1. An app that Can Find your Location automatically 
2. Can find your typed location
3. Plot these locations on the Map
4. Find and Display the venues around you 
4. Can tell you at what distance every value is located and other details about
5. Mark Red for Low Green for Good and Dark Green for Very Good Ratings of a Venues
6. You can search specific category and Trending venues around you aswell

### All The necessary Imports 

In [1]:
import json                               # library to handle JSON files
import folium                             # map rendering library
import requests                           # Handle Requests
import warnings                           # Ignore all th warning 
import numpy as np 
import pandas as pd 
import matplotlib.cm as cm
from matplotlib import pyplot as plt
import matplotlib.colors as colors
%matplotlib inline


from geopy.geocoders import Nominatim     # convert an address into latitude and longitude values
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe


from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
warnings.filterwarnings("ignore")

#### Define Foursquare Credentials and Version
https://developer.foursquare.com/

In [35]:
CLIENT_ID     = '****************' # add your Foursquare ID
CLIENT_SECRET = '****************' # add your Foursquare Secret
ACCESS_TOKEN  = '****************' # add your FourSquare Access Token
VERSION = '20180604'

### Get the location of Device Using 
#### https://mycurrentlocation.net/
#### Scrape the (Lat , Lon ) Cordinates 

In [37]:
# Return the Long. Lat. of the Your Current Location (Estimated)
def findmyLocation():
    chrome_options = Options()
    chrome_options.add_argument("--use-fake-ui-for-media-stream")
    timeout = 20
    driver = webdriver.Chrome(chrome_options=chrome_options,executable_path='F:\chromedriver.exe')
    driver.get("https://mycurrentlocation.net/")
    wait = WebDriverWait(driver, timeout)
    longitude = driver.find_elements_by_xpath('//*[@id="longitude"]')
    longitude = [x.text for x in longitude]
    longitude = str(longitude[0])
    latitude = driver.find_elements_by_xpath('//*[@id="latitude"]')
    latitude = [x.text for x in latitude]
    latitude = str(latitude[0])
    driver.quit()
    return (latitude,longitude)

# Find the Location which you Will give it to (Return the Long. Lat. of the added Location)
def findlocation():
    address = input("Please enter the Address : ")
    geolocator = Nominatim(user_agent="Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    return (latitude,longitude)


    ##### FUNCTION TO FIND THE RATING OF A VANUES (Return darkgreen if rating GREATER than 8 , Green if greater than 7 , Below 7 Red  )
def rating(VENUE_ID):
    url = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(
        VENUE_ID,
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION)
    results = requests.get(url).json()
    try:
        x=results['response']['venue']['rating']
        if x>= 8:
            return "darkgreen"
        elif x >= 6 and x < 8 :
            return 'blue'
        else:
            return 'red'
    except KeyError:
        return 'red'
    except:
        return 'red'

### Return the Venues JSON containing all the details about a Venues

def venues(latitude , longitude , LIMIT = 100 , radius = 500 ): # limit of number of venues returned by Foursquare API
    """ return the NAME,LOCATION,ID,CATAGORY of a venues """
 
                                         #venues, users , tips
                                                #search,explore,trending  if search then pass te query too                ,query={} coffe, hotels ,resturents etc
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET,
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)
    results = requests.get(url).json()
    if len(results["response"]["groups"][0]['items']) > 20 or radius > 2000 :
        return results
    else:
        return venues(latitude=latitude ,longitude=longitude,LIMIT = LIMIT , radius = radius+500 )
              


         # FUNCTION TO CLEAN THE JSON RESPONSE FROM THE FOURSQUARE API
def venues_clean(res):
    venues=res["response"]["groups"][0]['items'] # Extract the Venues JSON from the response 
    nearby_venues = json_normalize(venues) # flatten JSON and convert it into Pandas Dataframe
    data_df = nearby_venues[ [             # Filter Dataframe for the Required data of venues
    'venue.id','venue.name',
    'venue.categories',
    'venue.location.lat',
    'venue.location.lng',
    'venue.location.distance'] ]
    # Extract the catagory from the JSON 'venue.categories'
    data_df['venue.categories']=data_df['venue.categories'].apply( lambda x : x[0]["name"] )
    # Clean the name of Columns of Dataframe
    data_df.columns = [col.split(".")[-1] for col in data_df.columns]
    data_df["rating"]=data_df["id"].apply(rating)
    return data_df


##### Search Specific Catagory of Venues around a Location
def venues_cat(latitude ,longitude,search_query,LIMIT = 100 , radius = 1000 ): # limit of number of venues returned by Foursquare API
    """ return the NAME,LOCATION,ID,CATAGORY of venues """
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(
        CLIENT_ID,
        CLIENT_SECRET,
        latitude,
        longitude,
        VERSION,
        search_query,
        radius,
        LIMIT)     
    results = requests.get(url).json()
    
    """If There is no Venue of that catagory around then Increase the radius of Search by 500 meter and search again.
        Repeat this process until you find a nearest Veneu"""
    
    if len(results["response"]["venues"]) > 5 or radius > 5000 :
        return results
    else:
        return venues_cat(latitude=latitude ,longitude=longitude,search_query = search_query,LIMIT = LIMIT , radius = radius+500 )
    
#### CLEAN THE DATA OF SEARCH  
def venues_cat_clean(res):
    df=json_normalize(res['response']['venues'])
    df=df[['id','name','categories','location.lat','location.lng','location.distance']]
    lis=[]
    for i in df['categories']:
        try:
            lis.append(i[0]['name'])
        except:
            lis.append("_")
    df["categories"]=lis
    df.columns = [col.split(".")[-1] for col in df.columns]
    df["rating"]=df["id"].apply(rating)
    
    return df


#### SEARCH TRENDING VENEUS
def venues_tre(latitude,longitude): # limit of number of venues returned by Foursquare API
    """ return the NAME,LOCATION,ID,CATAGORY of a trending venues """
    url = 'https://api.foursquare.com/v2/venues/trending?&client_id={}&client_secret={}&ll={},{}&v={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET,  
        latitude, 
        longitude, 
        VERSION
        )
    results = requests.get(url).json()
    """If There is no trending Venue around Increase the radius of Search by 500 meter and search again.
    Repeat this process until you find a nearest Veneu"""
#     if len(results["response"]["venues"]) > 15 or radius > 10000:
    return results
#     else:
#         return venues_tre(latitude=latitude ,longitude=longitude , radius = radius+1000 )


def venues_tre_clean(res):
    df=json_normalize(res['response']['venues'])
    df=df[['id','name','categories','location.lat','location.lng','location.distance']]
    df.columns = [col.split(".")[-1] for col in df.columns]
    lis=[]
    for i in df['categories']:
        try:
            lis.append(i[0]['name'])
        except:
            lis.append("_")
    df["categories"]=lis
    df["rating"]=df["id"].apply(rating)
    return df



## FIND MY LOCATION 

In [31]:
latitude,longitude = findmyLocation()                  # Find the Location of Added Address
mapo=folium.Map(location=[latitude,longitude],zoom_start=13,tiles='Stamen Terrain') # Its Blank Canvass of Map
folium.Marker(location=[latitude,longitude],popup="Estimated Location",tooltip="Your Location",icon=folium.CustomIcon(icon_image="C:/Users/Abdul Rehman/Myloc.gif")).add_to(mapo)
mapo


## FIND A LOCATION

In [38]:
latitude,longitude = findlocation()                  # Find the Location of Added Address
mapobj1=folium.Map(location=[latitude,longitude],zoom_start=14) # Its Blank Canvass of Map
folium.Marker(location=[latitude,longitude],popup="Estimated Location",tooltip="Added Location",icon=folium.CustomIcon(icon_image="C:/Users/Abdul Rehman/loc.gif")).add_to(mapobj1)
mapobj1

Please enter the Address : Blue area Islamabad


## FIND High Rated VENUES AROUND

In [39]:
res                = venues(latitude,longitude)      # Find the venues around that Blue Area Islamabd (Entered Location)  
data_df            = venues_clean(res)               # Clean the Data 

In [40]:
data_df                                             # Show the data

id                              name  \
0   51b962c7498e1ba21d4ff958  Burning Brownie Cafe & Bake Shop   
1   587f30c375e1370bc443c588                             Crema   
2   4d3314f78c42a1cd92b9ee5d                      Chaaye Khana   
3   4d297779b818a35dda4a9f8a                             Shams   
4   51468fcae4b0136ab69b973e                   Pizza Originale   
5   4c1c844db9f876b0d4147c46                   Shaheen Chemist   
6   4bae3d26f964a520d6963be3                      Super Market   
7   5242f9fd11d247e41346dc2e                        F-6 Markaz   
8   4d5ba6629c31b60ca9e4abee                 The Oxygen Lounge   
9   5157fbe9e4b03dbb5ac90284                        Yogen Früz   
10  4c964b446b35a14304862cdc                Usmania Restaurant   
11  4f50c8cfe4b0b71c7953f0d1                     Salt n Pepper   
12  4c1c882efcf8c9b64640aa0b                           Nando's   
13  56791281498e5c3e854db77c              Cannoli by Cafe Soul   
14  4cde8a7741ed224b127dd93c                          Tiramisu   
15  4d7cb5fa645ea35d18a14af8                        Illusion's   
16  576059f3498eb0545217b260                       Khoka Khola   
17  4d8dff38d265236a21ecfe16            Omar Khayam Restaurant   
18  50c22fd0e4b0cd152590c317                 14th Street Pizza   
19  4bd576096798ef3b5553638d                     United Bakery   
20  4bae39f1f964a520f8943be3                     Melody Market   
21  4e131a988877ac23b66f5600      Food Street Melody Islamabad   
22  4bdc2d1263c5c9b6e5a12a68                        Best Price   
23  4bd048b4caff95216a7bcef0                       Pizza Party   
24  4bd1b8c4462cb713fbadda07                          Munchies   
25  4c94ccd482b56dcbdf42d2aa              American Steak House   
26  4eccb926cc215616122d927e                     Fijji's Grill   
27  4d176955e190721e8bba1a21                       BBQ Tonight   
28  4b65913cf964a520b5f42ae3                   Islamabad Hotel   
29  4f66004fe4b0ea77cedf9c81                        Bata Shoes   
30  4edb1fa7d3e346be35411ac7       Multi Purpose Sports Center   
31  56a7abb8498ec81a0cec5c50                       Naan Dhaaba   
32  5cd9a4b08afbe0002dc96a79                           Kaspa’s   
33  4b95349df964a520ef9434e3                          The Cave   
34  5d6acee2944868000860aacc                     Baskin-Robins   
35  4d5e96b7865a224bca2e9485                          Mr. Food   
36  4f5a1227e4b00984bddc1ca5             Islamabad Lights Shop   
37  4e84388c77c842a2599a6782                        Canon Link   

                categories        lat        lng  distance     rating  
0              Coffee Shop  33.720508  73.073956       479  darkgreen  
1                     Café  33.719849  73.073967       509       blue  
2                 Tea Room  33.729388  73.074913       892  darkgreen  
3                Gift Shop  33.729484  73.074870       903       blue  
4              Pizza Place  33.729395  73.074924       892       blue  
5                 Pharmacy  33.729805  73.075435       917       blue  
6              Flea Market  33.729724  73.075947       893       blue  
7                   Market  33.729729  73.075450       908       blue  
8               Hookah Bar  33.726932  73.087452       968       blue  
9       Frozen Yogurt Shop  33.729369  73.075757       861       blue  
10        Asian Restaurant  33.720501  73.078032       186       blue  
11    Pakistani Restaurant  33.719338  73.075647       419       blue  
12   Portuguese Restaurant  33.729953  73.078057       882       blue  
13      Italian Restaurant  33.720317  73.073682       511       blue  
14      Italian Restaurant  33.726377  73.086407       853       blue  
15       Electronics Store  33.729195  73.076270       828       blue  
16        Asian Restaurant  33.720196  73.073423       538       blue  
17              Restaurant  33.718592  73.073603       615       blue  
18             Pizza Place  33.727235  73.086628       926       blue  
19         

In [41]:
## Plotting these Venues 
for lat, lng, name, categories,distance,col in zip(data_df['lat'], data_df['lng'], data_df['name'], data_df['categories'],data_df['distance'],data_df['rating']):
    label = '{}, {}'.format(name, categories)
    folium.CircleMarker(
        [lat, lng],
        radius=6,
        tooltip=label,
        popup=str(distance)+"m away",
        color=col,
        fill=True,
        fill_color=col,
        fill_opacity=0.5).add_to(mapobj1)  
folium.TileLayer('openstreetmap',).add_to(mapobj1)
mapobj1

## SEARCH VENUES OF A CATAGORY 
We can add more catagories from **Here** https://developer.foursquare.com/docs/build-with-foursquare/categories/

In [42]:
search_query=input("Please Enter any of these \n Arts & Entertainment \n Museum \n Music Venue \n Stadium \n College & University \n Food \n Medical Center \n ")
res                = venues_cat(latitude,longitude,search_query)      # Find the venues of that catagory 
data_df            = venues_cat_clean(res)                            # Clean the Data 

Please Enter any of these 
 Arts & Entertainment 
 Museum 
 Music Venue 
 Stadium 
 College & University 
 Food 
 Medical Center 
 Food


In [43]:
data_df

id                                         name  \
0  4e131a988877ac23b66f5600                 Food Street Melody Islamabad   
1  520f8c2b11d2f3e74eee6c6a  Rana Bhai Pan Dan Walay, Melody Food Street   
2  4d5e96b7865a224bca2e9485                                     Mr. Food   
3  4fffe2e5e4b0c17e10a0bbb3                               Shinwari Foods   
4  507ea406e4b058f60a1ca191                               Shenwari Foods   
5  555ef062498e975fd3efcf17                                 Corner Foods   

               categories        lat        lng  distance rating  
0              Food Court  33.717217  73.084779       772    red  
1        Asian Restaurant  33.717162  73.084636       767    red  
2              Restaurant  33.730351  73.076973       938    red  
3               BBQ Joint  33.719299  73.074661       490    red  
4  Argentinian Restaurant  33.723965  73.087423       826    red  
5    Pakistani Restaurant  33.716545  73.085469       870    red

In [44]:
mapobj1=folium.Map(location=[latitude,longitude],zoom_start=14) # Its Blank Canvass of Map
folium.Marker(location=[latitude,longitude],popup="Estimated Location",tooltip="Added Location",icon=folium.CustomIcon(icon_image="C:/Users/Abdul Rehman/loc.gif")).add_to(mapobj1)
for lat, lng, name, categories,distance,col in zip(data_df['lat'], data_df['lng'], data_df['name'], data_df['categories'],data_df['distance'],data_df['rating']):
    label = '{}, {}'.format(name, categories)
    folium.CircleMarker(
        [lat, lng],
        radius=6,
        tooltip=label,
        popup=str(distance)+"m away",
        color=col,
        fill=True,
        fill_color=col,
        fill_opacity=0.5).add_to(mapobj1)  
folium.TileLayer('openstreetmap',).add_to(mapobj1)
mapobj1

## Search for Trending Venues Around 

In [45]:
res                = venues_tre(latitude,longitude)      # Find the venues trending
mapobj1=folium.Map(location=[latitude,longitude],zoom_start=14) # Its Blank Canvass of Map
folium.Marker(location=[latitude,longitude],popup="Estimated Location",tooltip="Added Location",icon=folium.CustomIcon(icon_image="C:/Users/Abdul Rehman/loc.gif")).add_to(mapobj1)

try:
    data_df            = venues_tre_clean(res)                            # Clean the Data 
    for lat, lng, name, categories,distance,col in zip(data_df['lat'], data_df['lng'], data_df['name'], data_df['categories'],data_df['distance'],data_df['rating']):
        label = '{}, {}'.format(name, categories)
        folium.CircleMarker(
        [lat, lng],
        radius=6,
        tooltip=label,
        popup=str(distance)+"m away",
        color=col,
        fill=True,
        fill_color=col,
        fill_opacity=0.5).add_to(mapobj1)  
    folium.TileLayer('openstreetmap',).add_to(mapobj1)
except:
    print("Sorry 😐! There is No trending Venue Around You\nTry other ways")
mapobj1


Sorry 😐! There is No trending Venue Around You
Try other ways


## THANK YOU!